In [1]:
import numpy as np
import pandas as pd
import string
import re
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
import pickle
from sklearn.decomposition import PCA
from sklearn.svm import SVC
import random
from sklearn.preprocessing import StandardScaler
random.seed(42)
from sklearn.metrics import silhouette_samples, silhouette_score
import matplotlib.cm as cm
import nlp_preparation as nlp
%load_ext autoreload
%autoreload 2

In [2]:
data = pd.read_csv('meh_data.csv', sep='\t')

In [225]:
names = data['item_name']

In [227]:
names.to_csv('names.csv', sep='\t')

In [4]:
data = data[['datetime','item_features','item_name','mehs','poll_num','sale_num','sale_revenue','story','visits']]

In [5]:
data['datetime'] = pd.to_datetime(data['datetime'])

In [6]:
data['item_name'] = data['item_name'].apply(lambda x: x.strip())

In [7]:
data_train, data_test = train_test_split(data)

In [306]:
data['price'] = (data['sale_revenue'] - 5 * data['sale_num'])/data['sale_num']

In [307]:
scaler = StandardScaler()
data['std_price'] =scaler.fit_transform(data[['price']])

In [308]:
data

datetime  \
0    2018-11-17 05:00:07.557   
1    2018-11-16 05:00:07.922   
2    2018-11-15 05:00:04.026   
3    2018-11-14 05:00:08.839   
4    2018-11-13 05:00:00.503   
5    2018-11-12 05:00:06.036   
6    2018-11-11 05:00:03.094   
7    2018-11-10 05:00:31.466   
8    2018-11-09 05:00:01.032   
9    2018-11-08 05:00:04.026   
10   2018-11-07 05:00:06.482   
11   2018-11-06 05:00:05.999   
12   2018-11-05 05:00:09.745   
13   2018-11-04 04:00:05.099   
14   2018-11-03 04:00:03.903   
15   2018-11-02 04:00:05.893   
16   2018-11-01 04:00:05.247   
17   2018-10-31 04:00:04.899   
18   2018-10-30 04:00:07.136   
19   2018-10-29 04:00:09.519   
20   2018-10-28 04:00:02.109   
21   2018-10-27 04:00:12.340   
22   2018-10-26 04:00:03.801   
23   2018-10-25 04:00:09.038   
24   2018-10-24 04:00:06.142   
25   2018-10-23 04:00:01.475   
26   2018-10-22 04:00:03.164   
27   2018-10-21 04:00:03.298   
28   2018-10-20 04:00:46.966   
29   2018-10-19 04:00:01.945   
...                      ...   
1677 2014-08-28 04:00:01.265   
1678 2014-08-27 04:00:01.374   
1679 2014-08-26 04:00:01.851   
1680 2014-08-25 03:59:59.499   
1681 2014-08-24 04:00:00.802   
1682 2014-08-22 04:00:01.984   
1683 2014-08-21 04:00:01.538   
1684 2014-08-20 04:00:01.535   
1685 2014-08-19 04:00:01.270   
1686 2014-08-18 04:00:01.321   
1687 2014-08-15 04:00:01.425   
1688 2014-08-14 04:00:00.465   
1689 2014-08-13 04:00:00.662   
1690 2014-08-12 04:00:00.501   
1691 2014-08-11 04:00:00.316   
1692 2014-08-10 04:00:00.304   
1693 2014-08-09 04:00:00.764   
1694 2014-08-08 04:00:00.509   
1695 2014-08-04 04:00:01.393   
1696 2014-07-30 04:00:01.171   
1697 2014-07-28 04:00:00.962   
1698 2014-07-27 04:00:01.241   
1699 2014-07-26 04:00:01.229   
1700 2014-07-24 04:00:01.717   
1701 2014-07-19 04:00:01.879   
1702 2014-07-16 04:00:01.117   
1703 2014-07-15 04:00:00.693   
1704 2014-07-14 04:00:01.287   
1705 2014-07-10 04:00:01.199   
1706 2014-07-09 04:00:00.704   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              item_features  \
0     These are pens that can project designs out of their butts.\nYou can get 4 of same kind for $10, or all 12 different ones for $20.\nIt feels like forever since I’ve had to write about a projector. It’s good to be back, baby.\nModel numbers: 1INKIW4116-00, 1INKIW4142-00, 1INKIW4154-00, 1INKIW4134-00, 1INKIW4150-00, ST1NKYF4RT-00, 1INKIW4143-00, 1INKIW4157-00, 1INKIW4144-00, 1INKIW4136-00, 1INKIW4152-00, 1INKIW4149-00, 1INKIW4110-00. Now, let’s play a round of spot the fake model number!                                                                                                                                                                                                                                                                                                              
1     You get a pendant, a set of earrings, and a ring to match.\nThis holiday season, get that special someone something creative, something that’ll blow their mind on Christmas morning…\nOr get them this.\nHonestly, it’s way less risky.\nModel: BOR458M, BOR471M, BOR595M, BOR629M, BOR863M. And they each include a ring. But they’re anything but BOR-ring.                                                                                 

In [309]:
nlp_names = nlp.nlp_content(data['item_name'])
nlp_specs = nlp.nlp_content(data['item_features'])

In [310]:
descriptions = nlp.create_description(nlp_names,nlp_specs)

In [311]:
data['descriptions'] = descriptions.values

In [312]:
data['nlp_story'] = nlp.nlp_content(data['story']).values

In [313]:
data

datetime  \
0    2018-11-17 05:00:07.557   
1    2018-11-16 05:00:07.922   
2    2018-11-15 05:00:04.026   
3    2018-11-14 05:00:08.839   
4    2018-11-13 05:00:00.503   
5    2018-11-12 05:00:06.036   
6    2018-11-11 05:00:03.094   
7    2018-11-10 05:00:31.466   
8    2018-11-09 05:00:01.032   
9    2018-11-08 05:00:04.026   
10   2018-11-07 05:00:06.482   
11   2018-11-06 05:00:05.999   
12   2018-11-05 05:00:09.745   
13   2018-11-04 04:00:05.099   
14   2018-11-03 04:00:03.903   
15   2018-11-02 04:00:05.893   
16   2018-11-01 04:00:05.247   
17   2018-10-31 04:00:04.899   
18   2018-10-30 04:00:07.136   
19   2018-10-29 04:00:09.519   
20   2018-10-28 04:00:02.109   
21   2018-10-27 04:00:12.340   
22   2018-10-26 04:00:03.801   
23   2018-10-25 04:00:09.038   
24   2018-10-24 04:00:06.142   
25   2018-10-23 04:00:01.475   
26   2018-10-22 04:00:03.164   
27   2018-10-21 04:00:03.298   
28   2018-10-20 04:00:46.966   
29   2018-10-19 04:00:01.945   
...                      ...   
1677 2014-08-28 04:00:01.265   
1678 2014-08-27 04:00:01.374   
1679 2014-08-26 04:00:01.851   
1680 2014-08-25 03:59:59.499   
1681 2014-08-24 04:00:00.802   
1682 2014-08-22 04:00:01.984   
1683 2014-08-21 04:00:01.538   
1684 2014-08-20 04:00:01.535   
1685 2014-08-19 04:00:01.270   
1686 2014-08-18 04:00:01.321   
1687 2014-08-15 04:00:01.425   
1688 2014-08-14 04:00:00.465   
1689 2014-08-13 04:00:00.662   
1690 2014-08-12 04:00:00.501   
1691 2014-08-11 04:00:00.316   
1692 2014-08-10 04:00:00.304   
1693 2014-08-09 04:00:00.764   
1694 2014-08-08 04:00:00.509   
1695 2014-08-04 04:00:01.393   
1696 2014-07-30 04:00:01.171   
1697 2014-07-28 04:00:00.962   
1698 2014-07-27 04:00:01.241   
1699 2014-07-26 04:00:01.229   
1700 2014-07-24 04:00:01.717   
1701 2014-07-19 04:00:01.879   
1702 2014-07-16 04:00:01.117   
1703 2014-07-15 04:00:00.693   
1704 2014-07-14 04:00:01.287   
1705 2014-07-10 04:00:01.199   
1706 2014-07-09 04:00:00.704   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              item_features  \
0     These are pens that can project designs out of their butts.\nYou can get 4 of same kind for $10, or all 12 different ones for $20.\nIt feels like forever since I’ve had to write about a projector. It’s good to be back, baby.\nModel numbers: 1INKIW4116-00, 1INKIW4142-00, 1INKIW4154-00, 1INKIW4134-00, 1INKIW4150-00, ST1NKYF4RT-00, 1INKIW4143-00, 1INKIW4157-00, 1INKIW4144-00, 1INKIW4136-00, 1INKIW4152-00, 1INKIW4149-00, 1INKIW4110-00. Now, let’s play a round of spot the fake model number!                                                                                                                                                                                                                                                                                                              
1     You get a pendant, a set of earrings, and a ring to match.\nThis holiday season, get that special someone something creative, something that’ll blow their mind on Christmas morning…\nOr get them this.\nHonestly, it’s way less risky.\nModel: BOR458M, BOR471M, BOR595M, BOR629M, BOR863M. And they each include a ring. But they’re anything but BOR-ring.                                                                                 

In [314]:
tfidf_dscrp = nlp.tfidf_content(data['descriptions'])
tfidf_story = nlp.tfidf_content(data['nlp_story'])

In [315]:
tfidf_dscrp.set_index(data.index,inplace = True)
tfidf_dscrp['item_name'] = data['item_name']
tfidf_story.set_index(data.index,inplace = True)
tfidf_story['item_name'] = data['item_name']

# Clustering only use descriptions feature

In [19]:
# model with tfidf description only
pca = PCA(3)
transformed_dscrp = pca.fit_transform(tfidf_dscrp.drop(columns = 'item_name'))
kmeans = KMeans(n_clusters=6)
kmeans.fit(transformed_dscrp)
tfidf_dscrp['cluster'] = kmeans.labels_

In [23]:
tfidf_dscrp

0    1    2    3    4    5    6    7         8    9   ...     10556  \
366   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1039  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
634   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
984   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
524   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
955   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
663   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1374  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1633  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
68    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1363  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
325   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1436  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1636  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1261  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1273  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
830   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1291  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
17    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
586   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1589  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
930   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
51    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1185  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1135  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1057  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1422  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
270   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1667  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1157  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
...   ...  ...  ...  ...  ...  ...  ...  ...       ...  ...   ...       ...   
65    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
90    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1094  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
253   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
102   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1233  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
550   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
133   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1462  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
3     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
299   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
836   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.178473  0.0   ...       0.0   
471   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
532   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
101   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1154  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1256  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1546  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.0   ...       0.0   
1558  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.

In [38]:
tfidf_dscrp[tfidf_dscrp['cluster']==0]['item_name']

366            2-for-Tuesday: Duncan Groove Yo-yo Kendama
1039                Meh Shirt with Frosting and Sprinkles
984               Liquid Image 720p Action Camera Goggles
524                                   Enderson Bag Bundle
955              Toshiba 13.3" Chromebook 2 (Refurbished)
663                Makey Makey Invention Kit for Everyone
1374         Capresso 4-Cup Espresso & Cappuccino Machine
1363    Pursonic S20 UV Family Toothbrush Sanitizer w/...
325     Zmodo Greet WiFi Video Doorbell with Zmodo Bea...
1273                2-for-Tuesday: Snap Activity Trackers
830             Foscam FI9803P Outdoor Wireless IP Camera
17      Pure Enrichment Hume Ultrasonic Cool Mist Humi...
586          ImogenStudio +Cam Outdoor HD Security Camera
51                     360FLY 360-Degree HD Action Camera
1185                                     Belding Golf Bag
1135    350 Thread Count Down Alternative Pillows (Set...
1057          2-for-Tuesday: Pure Copper Moscow Mule Mugs
1422        KR

In [39]:
tfidf_dscrp[tfidf_dscrp['cluster']==1]['item_name']

270    Fukobukuro 19: Fools Rush In
266    Fukobukuro 19: Fools Rush In
241    Fukobukuro 19: Fools Rush In
267    Fukobukuro 19: Fools Rush In
283    Fukobukuro 19: Fools Rush In
279    Fukobukuro 19: Fools Rush In
248    Fukobukuro 19: Fools Rush In
268    Fukobukuro 19: Fools Rush In
275    Fukobukuro 19: Fools Rush In
262    Fukobukuro 19: Fools Rush In
280    Fukobukuro 19: Fools Rush In
277    Fukobukuro 19: Fools Rush In
265    Fukobukuro 19: Fools Rush In
235    Fukobukuro 19: Fools Rush In
258    Fukobukuro 19: Fools Rush In
247    Fukobukuro 19: Fools Rush In
281    Fukobukuro 19: Fools Rush In
244    Fukobukuro 19: Fools Rush In
232    Fukobukuro 19: Fools Rush In
278    Fukobukuro 19: Fools Rush In
263    Fukobukuro 19: Fools Rush In
250    Fukobukuro 19: Fools Rush In
257    Fukobukuro 19: Fools Rush In
246    Fukobukuro 19: Fools Rush In
282    Fukobukuro 19: Fools Rush In
252    Fukobukuro 19: Fools Rush In
273    Fukobukuro 19: Fools Rush In
260    Fukobukuro 19: Fools 

In [148]:
# The unlucky bags
tfidf_dscrp.groupby('cluster').groups[1]

Index(['Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
       'Fukobukuro 19: Fools Rush In', 'Fukobukuro 19: Fools Rush In',
      

In [40]:
tfidf_dscrp[tfidf_dscrp['cluster']==2]['item_name']

634     Philips Hue Starter Kit 2nd Generation (Refurb...
68                       iJoy 10,000 mAh Jump Starter Kit
1436                                   Meta M1 Smartwatch
1261                  Looney Tunes 8GB USB 2.0 MP3 Player
1589    2-for-Tuesday: JLab Hi-Fi Noise-Reducing Ear Buds
1667              iPhone Charger & Sound Embiggener Stand
1157           Monster Inspiration Lite On-Ear Headphones
506     Energizer 600A 11,100mAh UL-Listed Lithium Jum...
713      General ToolSmart Bluetooth Digital Angle Finder
207     4-for-Tuesday: XYON Triple-Outlet Adapters wit...
334                 4-Pack: Neo Style 6000mAh Power Banks
778            2-for-Tuesday: Ivy USB Port LED Desk Lamps
108        Cyntur JumperPack Mini Lithium-Ion Jumpstarter
638                           Bem Strum Bluetooth Speaker
1076                               Pulse Massager Mini II
802                                 4ID LED Lite Up Leash
42        Xsories Sneaker Power Bank and Dual USB Charger
1678          

In [149]:
tfidf_dscrp.groupby('cluster').groups[2]

Index(['MOTA JetJat Ultra FPV Drone', 'Polk Audio N1 39" Bluetooth Soundbar',
       'Pronto and Peel Smart Universal Remote Control',
       'House of Marley Liberate Bluetooth Headphones',
       'Monster Inspiration Active Noise Canceling Over-Ear Headphones',
       '808 Audio DUO Wired + Wireless Headphones', 'Bēm Wrist Speaker',
       '2-for-Tuesday: Bracketron Twist and Charge USB Chargers',
       'Turtle Beach Ear Force i60 Wireless Gaming Headset with 7.1 Surround Sound',
       'Zipstick 2200mAh Rechargeable Power Bank',
       ...
       '12-for-Tuesday: Powrtabs Emergency Chargers',
       'Cobra 800W Power Inverter (Refurbished)',
       '2-for-Tuesday: Boom Swap On/Over-Ear Headphones',
       'Batband Ear-Free Wireless Hearable', 'Meta M1 Smartwatch',
       'Envic Unlocked Android Phone & Smartwatch Bundle',
       'Freshebuds Air Magnetic Bluetooth Earbuds',
       'Panasonic Eneloop Battery Power Pack', 'Ion Audio Party Bot Micro',
       'Powerbeats2 Wireless Headp

In [41]:
tfidf_dscrp[tfidf_dscrp['cluster']==3]['item_name']

1291         J.A. Henckels Mikado 4-Piece Steak Knife Set
808     Mad Hungry 4-Piece Air Blade Knife Set with Kn...
521            Stupid Crap We Always Sell But In A Bundle
1514    2-for-Tuesday: Chicago Cutlery Walnut Traditio...
1158             Kershaw 3820 Injection 3.0 Folding Knife
975                Mad Hungry 4-Piece Air Blade Knife Set
1502    Cuisinart 13-Piece Graphix Collection Knife Bl...
1384      Oneida Stainless Steel Steak Knife Set (4-Pack)
1047                         Ginsu Nuri 3-Piece Knife Set
1688                Cuisinart Knife Set and Acrylic Stand
945                             CRKT Get.Shit.Done. Knife
657                             Quikut 20-Piece Knife Set
909                                  CRKT Tighe Rod Knife
1227         J.A. Henckels Mikado 4-Piece Steak Knife Set
1345               Cuisinart Advantage 12-Piece Knife Set
595                            Kai Luna 6-Piece Knife Set
1625         Kershaw Funxion Outdoor Knife with Saw Blade
1516          

In [150]:
# Speakers
tfidf_dscrp.groupby('cluster').groups[3]

Index(['CRKT Get.Shit.Done. Knife', 'Mad Hungry 4-Piece Air Blade Knife Set',
       'Kai Inspire 5-Piece Cutlery Set', 'Kai Luna 6-Piece Knife Set',
       'Mad Hungry 4-Piece Air Blade Knife Set with Knish Knife Sharpener',
       'Ginsu Nuri 3-Piece Knife Set',
       'Cuisinart 13-Piece Graphix Collection Knife Block Set',
       'J.A. Henckels Mikado 4-Piece Steak Knife Set',
       'Zwilling J.A. Henckels 6-Piece Knife Block Set',
       '2-for-Tuesday: Chicago Cutlery Walnut Tradition Steak Knife Sets',
       'Quikut 20-Piece Knife Set'],
      dtype='object', name='item_name')

In [42]:
tfidf_dscrp[tfidf_dscrp['cluster']==4]['item_name']

1633    JBL OnBeat Mini iPhone/iPad Portable Speaker Dock
1636                            Palo Alto Rhombus Speaker
930                  Pioneer Dolby Atmos Enabled Speakers
1180    Ion Audio Sound Splash Bluetooth Speaker with ...
1136          Bluetooth Outlet Speaker with 2.1A USB Port
1568    2-for-Tuesday: Justin Tablet Case with Bluetoo...
734              QFX Elite Series WiFi+Bluetooth Speakers
723                   2-Pack: Que Wifi/Bluetooth Speakers
1203    2-for-Tuesday: Ion Audio Clipster Outdoor Blue...
1131                           X-Mini Max Stereo Speakers
502     Sphereo True Wireless Stereo Bluetooth Speaker...
1683                 Crosley Trio Bluetooth Stereo System
953       2-for-Tuesday: iFrogz Active Bluetooth Speakers
773     2-Pack iLive Bluetooth Buddy Animatronic Anima...
10         Portable Echo Dot Speaker Dock with Power Bank
1270      Bem Academia Desk Lamp Bluetooth Speaker Thingy
1694    JBL OnBeat Mini or JBL OnBeat Micro Speaker Do...
1342    BEM Ac

In [151]:
# Accessories, mostly for phones
tfidf_dscrp.groupby('cluster').groups[4]

Index(['JBL OnBeat Micro Speaker Dock with Lightning Connector',
       'Bem Bravo Bluetooth Speaker',
       'Braven 705 Bluetooth Speaker with 1400mAh Battery',
       '2-for-Tuesday: iFrogz Active Bluetooth Speakers',
       'QFX Elite Series WiFi+Bluetooth Speakers', 'Bēm Bluetooth Speaker',
       'X-Mini Max Stereo Speakers',
       '2-for-Tuesday: Bem Mini Bluetooth Speakers',
       '2-for-Tuesday: QFX E-200 Portable WiFi + Bluetooth Multi-Room Speakers',
       'Monster ClarityHD Micro Bluetooth Speaker',
       'Gear Head Bluetooth Headphones',
       'Philips Bluetooth 2.0 Bookshelf Speakers',
       'Que Bluetooth Over-Ear Noise Canceling Headphones',
       'JBL OnBeat Mini and/or Micro Speaker Dock with Lightning Connector',
       'Speaker Dock, um, Sunday?: Hale Speaker Dock',
       'BEM Academia Wireless Bluetooth Desk Lamp and Speaker',
       'Urge Basics Soundbrick Bluetooth Stereo Speaker',
       'Pioneer Dolby Atmos Bookshelf Speakers',
       '2-for-Tuesday: Sm

In [152]:
tfidf_story.groupby('cluster').groups[5]

Index(['Poo Dough', 'Picnic Time Stratus Insulated Cooler w/ Wine Compartment',
       'Cheerson CX-10C Video Cam Quadcopter w/ SD Card Bundle',
       'The Big Backyard Portable Barbecue Grill & Cooler Bag',
       'LEGO Star Wars Millennium Falcon 75105',
       'Fukobukuro: Meh-rathon Edition',
       'Bem Freedom Bluetooth Headphone with Mic',
       '3-Pack: Xela Premium Soy Blend 7.5oz 30-Hour Candles',
       'Que Bluetooth In-Ear Headphones',
       'GT-Lite Motion Sensing 70FT 180º LED Security Light',
       'Random Meh (Or Whatever We Have Lying Around) Shirt',
       'Readymax 10" & 12" Tongue and Groove Pliers with Built-in LED Light',
       '2-Pack: Mini Compact "Travel Massager"',
       'General ToolSmart Bluetooth Digital Angle Finder',
       'Shark Rotator Powered Lift-Away Vacuum (Refurbished)',
       'PowerNow 10,000mAh 2.1A Power Bank',
       '2-Pack: QFX E-200 Portable WiFi + Bluetooth Multi-Room Speakers',
       'Fosbaby Digital Video Baby Monitor', 'Stinky 

In [159]:
# n_clusters=6 gives the best score
silhouette_avg = silhouette_score(transformed_dscrp, tfidf_dscrp['cluster'])
silhouette_avg

0.5625239052830843

# Clustering only using story feature

In [43]:
tfidf_story

0    1    2    3    4         5    6    7    8    9  \
366   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1039  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
634   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
984   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
524   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
955   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
663   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1374  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1633  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
68    0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1363  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
325   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1436  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1636  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1261  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1273  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
830   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1291  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
17    0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
586   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1589  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
930   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
51    0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1185  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1135  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1057  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1422  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
270   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1667  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1157  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
...   ...  ...  ...  ...  ...       ...  ...  ...  ...  ...   
65    0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
90    0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1094  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
253   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
102   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1233  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
550   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
133   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1462  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
3     0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
299   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
836   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
471   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
532   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
101   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1154  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1256  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1546  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1558  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
215   0.0  0.0  0.0  0.0  0.0  0.018877  0.0  0.0  0.0  0.0   
148   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1347  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1434  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
91    0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
700   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
641   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
906   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
742   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
740   0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   
1207  0.0  0.0  0.0  0.0  0.0  0.000000  0.0  0.0  0.0  0.0   

                            ...                             22800     22801  \
366                   

In [44]:
# model with tfidf story only
pca = PCA(3)
transformed_story = pca.fit_transform(tfidf_story.drop(columns='item_name'))
kmeans = KMeans(n_clusters=7)
kmeans.fit(transformed_story)
tfidf_story['cluster'] = kmeans.labels_

In [45]:
tfidf_dscrp[tfidf_story['cluster']==0]['item_name']

1633    JBL OnBeat Mini iPhone/iPad Portable Speaker Dock
930                  Pioneer Dolby Atmos Enabled Speakers
1667              iPhone Charger & Sound Embiggener Stand
1136          Bluetooth Outlet Speaker with 2.1A USB Port
638                           Bem Strum Bluetooth Speaker
734              QFX Elite Series WiFi+Bluetooth Speakers
723                   2-Pack: Que Wifi/Bluetooth Speakers
953       2-for-Tuesday: iFrogz Active Bluetooth Speakers
127         Zen Logic Wireless Speaker/Power Bank Bundles
1270      Bem Academia Desk Lamp Bluetooth Speaker Thingy
1694    JBL OnBeat Mini or JBL OnBeat Micro Speaker Do...
1692                          Palo Alto Cubik HD Speakers
1372    JBL OnBeat Micro Speaker Dock with Lightning C...
1495                     Denon Tabletop Bluetooth Speaker
1687                     Meh Shirt.....and a Speaker Dock
974            2-for-Tuesday: Bēm Mini Bluetooth Speakers
1153            Philips Bookshelf Speakers with Bluetooth
1366        Ab

In [46]:
tfidf_dscrp[tfidf_story['cluster']==1]['item_name']

366            2-for-Tuesday: Duncan Groove Yo-yo Kendama
634     Philips Hue Starter Kit 2nd Generation (Refurb...
984               Liquid Image 720p Action Camera Goggles
524                                   Enderson Bag Bundle
955              Toshiba 13.3" Chromebook 2 (Refurbished)
1374         Capresso 4-Cup Espresso & Cappuccino Machine
68                       iJoy 10,000 mAh Jump Starter Kit
1363    Pursonic S20 UV Family Toothbrush Sanitizer w/...
325     Zmodo Greet WiFi Video Doorbell with Zmodo Bea...
1273                2-for-Tuesday: Snap Activity Trackers
830             Foscam FI9803P Outdoor Wireless IP Camera
17      Pure Enrichment Hume Ultrasonic Cool Mist Humi...
1185                                     Belding Golf Bag
1135    350 Thread Count Down Alternative Pillows (Set...
1422        KRUPS Programmable Coffee Maker (Refurbished)
1674                                  Vornado Midsize Fan
1238    2-for-Tuesday: Life Gear Auto Emergency Tool L...
290           

In [47]:
tfidf_dscrp[tfidf_story['cluster']==2]['item_name']

687                           RoboSmasherz Fighting Game
688                       Fukobukuro: Meh-rathon Edition
682    SteelSeries Arctis 3 Universal Gaming Headset ...
690    Bem Mojo 16-Hour Bluetooth Speaker w/ Wireless...
689    Battlefield 1 Exclusive Collector's Edition (N...
681                  2-Pack: Ivy USB Port LED Desk Lamps
679                                     12oz Meh Tumbler
692    Apple Watch Series 2 38mm Space Gray / Black N...
680    Minx NY Socks for the Fam (Men's, Women's & Kids)
678           GoPro Hero4 Session HD 1080P Action Camera
691    Cheerson CX-10C Video Cam Quadcopter w/ SD Car...
686              Olio Model One Smartwatch (Refurbished)
685                2-Pack: LED Bluetooth Fidget Spinners
693            Weston Deluxe Heavy Duty #32 Meat Grinder
Name: item_name, dtype: object

In [48]:
tfidf_dscrp[tfidf_story['cluster']==3]['item_name']

1291         J.A. Henckels Mikado 4-Piece Steak Knife Set
1463                            Kershaw Funxion EMT Knife
1514    2-for-Tuesday: Chicago Cutlery Walnut Traditio...
1158             Kershaw 3820 Injection 3.0 Folding Knife
882              2-for-Tuesday: Remington Lockback Knives
1035                            Schrade Fixed Blade Knife
975                Mad Hungry 4-Piece Air Blade Knife Set
1502    Cuisinart 13-Piece Graphix Collection Knife Bl...
1526         Kershaw Funxion Outdoor Knife with Saw Blade
1083                            Kershaw Funxion EMT Knife
1282                 Kershaw Asset Assisted Opening Knife
1047                         Ginsu Nuri 3-Piece Knife Set
1688                Cuisinart Knife Set and Acrylic Stand
348                          Good / Better / Best Cutlery
945                             CRKT Get.Shit.Done. Knife
657                             Quikut 20-Piece Knife Set
1145                              SOG Contractor IV Knife
909           

In [49]:
tfidf_dscrp[tfidf_story['cluster']==4]['item_name']

1039                Meh Shirt with Frosting and Sprinkles
1436                                   Meta M1 Smartwatch
1636                            Palo Alto Rhombus Speaker
1261                  Looney Tunes 8GB USB 2.0 MP3 Player
1589    2-for-Tuesday: JLab Hi-Fi Noise-Reducing Ear Buds
51                     360FLY 360-Degree HD Action Camera
1057          2-for-Tuesday: Pure Copper Moscow Mule Mugs
1157           Monster Inspiration Lite On-Ear Headphones
1180    Ion Audio Sound Splash Bluetooth Speaker with ...
1368        2-for-Tuesday: InSite Locator and Transmitter
1568    2-for-Tuesday: Justin Tablet Case with Bluetoo...
334                 4-Pack: Neo Style 6000mAh Power Banks
1693    Swann Atom HD 1080P Wearable Action Camera w/ ...
778            2-for-Tuesday: Ivy USB Port LED Desk Lamps
1571                 Panasonic Sonic Vibration Toothbrush
1000    Unlocked Samsung Galaxy S6 32GB Smartphone (Re...
42        Xsories Sneaker Power Bank and Dual USB Charger
304           

In [50]:
tfidf_dscrp[tfidf_story['cluster']==5]['item_name']

586         ImogenStudio +Cam Outdoor HD Security Camera
270                         Fukobukuro 19: Fools Rush In
266                         Fukobukuro 19: Fools Rush In
431             Ashen Crossbody Bags by Parinda Handbags
584                      GoWISE Induction Plate with Pot
241                         Fukobukuro 19: Fools Rush In
267                         Fukobukuro 19: Fools Rush In
283                         Fukobukuro 19: Fools Rush In
410                    Fukobukuro 18: Meh-rathon Edition
279                         Fukobukuro 19: Fools Rush In
416    iON Cool-iCam S3000 Waterproof Action Camera w...
432    Oster Brawley 10-Piece Non-Stick Hard Anodized...
248                         Fukobukuro 19: Fools Rush In
268                         Fukobukuro 19: Fools Rush In
582                      GoPro HERO5 Black 4K Action Cam
448         2-Pack: Bra Society Silicone Push Up Inserts
275                         Fukobukuro 19: Fools Rush In
262                         Fuk

In [51]:
tfidf_dscrp[tfidf_story['cluster']==6]['item_name']

663               Makey Makey Invention Kit for Everyone
713     General ToolSmart Bluetooth Digital Angle Finder
666                     4ID LED Dog Leash & Collar Combo
665    3-Pack: Xela Premium Soy Blend 7.5oz 30-Hour C...
662                                     CRKT Argus Knife
669    Picnic Time Stratus Insulated Cooler w/ Wine C...
715                      Que Bluetooth In-Ear Headphones
704    3-Pack: Disney Infinity Figures Or Hasbro Star...
711    GT-Lite Motion Sensing 70FT 180º LED Security ...
710                   Fosbaby Digital Video Baby Monitor
708    2-Pack: QFX E-200 Portable WiFi + Bluetooth Mu...
714                    Fukobukuro 16: Meh-rathon Edition
674                    3-Pack: Sky Shredder Flying Discs
701                                  Stinky Waffle Robes
695                        BIOS Bullet 5.0 HD Action Cam
670                   PowerNow 10,000mAh 2.1A Power Bank
703               2-Pack: Mini Compact "Travel Massager"
712                            

In [52]:
# n_clusters=7 gives the best score
silhouette_avg = silhouette_score(transformed_story, tfidf_story['cluster'])
silhouette_avg

0.4653676376317247

# Clustering using all text features of the dataset, including item_name, item_features, story, best for layer 1

In [316]:
dd = pd.concat([data['descriptions'],data['nlp_story']], axis=1)
dd['item_name'] = data['item_name']
all_text = dd.apply( lambda x: x.descriptions + x.nlp_story, axis=1)

In [318]:
len(all_text)

1707

In [124]:
pd.DataFrame(all_text)

0
366   [tuesday, duncan, groove, yo, yo, kendama, get, kendama, yo, yo, combo, price, normal, kendama, uninitiated, kendamas, japanese, toy, sweeping, america, youth, culture, like, many, pokemon, tamagotchi, made, duncan, classic, toy, manufacturer, help, turn, yo, yo, perfect, valentine, gift, idiot, model, 3860ke, although, hope, america, future, fade, day, good, see, child, exposed, high, quality, model, number, early, age, dama, drama, know, broke, know, fear, peeking, credit, card, statement, beholding, december, wrought, know, told, going, buy, worthless, crap, least, month, worthless, crap, cheap, last, time, sold, pack, kendamas, sold, em, today, hewn, price, half, know, broke, c, mon, fact, duncan, groove, kendamas, ...]                                                                                       
1039  [meh, shirt, frosting, sprinkle, eat, matter, delicious, look, mark, momentous, occasion, second, birthday, seriously, need, reminder, time, next, year, like, dunno, last, birthday, always, american, apparel, men, size, run, small, woman, size, run, extra, small, 2xl, 3xl, two, buck, cost, u, two, buck, model, sci, fi, classic, antidepressant, somehow, fitting, u, two, ing, hey, second, birthday, would, thought, day, two, year, ago, still, today, aside, fact, went, pretty, much, exactly, thing, ten, year, earlier, woot, mean, even, though, reincarnation, feel, vaguely, familiar, probably, still, good, time, check, make, sure, toddling, website, maturing, physically, emotionally, intellectually, way, healthy, year, old, let, ...]                                                                                  
634   [philip, hue, starter, kit, 2nd, generation, refurbished, hub, two, bulb, make, home, least, lamp, smart, set, timer, control, light, phone, generally, feel, like, mr, smarty, mcsmarthome, controlled, alexa, siri, proprietary, voice, recognition, ai, technology, work, apple, homekit, first, smarthome, rodeo, white, light, going, make, joke, recent, justice, department, investigation, discrimination, white, model, recommend, setting, password, every, cyberhacker, planet, breaking, mainframe, dicking, light, side, sam, phillips, today, product, company, named, philip, offering, starter, kit, change, way, see, shed, new, light, home, today, weekend, playlist, producer, named, phillips, started, genre, change, way, hear, shed, new, light, ok, screw, contrived, intro, meh, contributor, ...]                        
984   [liquid, image, 720p, action, camera, goggles, goggles, camera, built, look, closely, photo, see, one, goggle, style, basic, black, frame, printed, pattern, around, lens, ask, good, either, camera, goggles, kind, missing, point, fine, camera, 720p, degree, lens, record, sd, card, included, goggles, standard, skiing, motorcycle, goggles, model, 384blk, product, goofy, model, number, tight, nice, work, fella, maybe, give, ridiculous, gadget, idea, start, model, numbering, consultancy, whopperrito, burger, king, caused, commotion, whopperrito, huh, ultimate, burger, burrito, mashup, irresistibly, awful, great, idea, help, get, sucked, promo, spiral, commenting, one, way, another, whopper, burrito, awesome, disgusting, get, yep, lot, people, talking, whopperrito, lot, ever, ...]                                   
524   [enderson, bag, bundle, get, bag, size, briefcase, size, toiletry, bag, made, water, repellent, ballistic, nylon, ballistic, repellent, kind, silly, website, worth, gander, handle, even, toiletry, bag, reason, perfect, sitting, next, hand, held, pensively, chin, model, includes, zip, code, range, kentucky, louisiana, presumably, draft, state, classy, reputation, everything, need, know, learned, lemonade, stand, gotta, feel, bad, enderson, bagware, name, sound, like, shopkeeper, elder, scroll, game, though, unfortunate, made, good, product, flopped, ended, retail, slaughterhouse, grating, meh, com, happen, well, made, product, fail, today, hyper, competitive, open, market, wel

In [319]:
data['item_name']

0       4-or-12-pack: Inkworks Projector Pens                                         
1       Pacific Pearls 3-Piece Pendant, Ring, and Earrings Gift Set                   
2       Pick 4: Angry Mills Protein-Infused Caffeinated Nut Spreads                   
3       NOTILUS Antimicrobial 3-in-1 Rain Shower Spa Combo                            
4       2-for-Tuesday: Bogui Wallets with or without RFID Cards                       
5       Polk Nue Era Headphones                                                       
6       ☕ The Process Shirt And/Or ☕ The Dream Shirt                                  
7       Grilling Traditions 3-Piece Pizza Stone Set                                   
8       18K Gold-Plated Heart Pendant with Diamond (1 Sapphire OR 1 Sapphire & 1 Ruby)
9       Primula Cold Brew Coffee Maker with 2 Travel Brewers                          
10      Portable Echo Dot Speaker Dock with Power Bank                                
11      2-for-Tuesday: Power Precision Sous

In [320]:
tfidf_all_text = nlp.tfidf_content(all_text)
tfidf_all_text['item_name']=data['item_name']

In [323]:
layer1_pca_3 = PCA(3)
layer1_pca_2 = PCA(2)
layer1_kmeans = KMeans(n_clusters=5)
transformed_text = layer1_pca_3.fit_transform(tfidf_all_text.drop(columns = ['item_name']))
kmeans.fit(transformed_text)
tfidf_all_text['cluster'] = kmeans.labels_

In [324]:
tfidf_all_text

0    1    2    3    4    5    6    7    8    9   ...     29776  \
0     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
2     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
3     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
4     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
5     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
6     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
7     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
8     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
9     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
10    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
11    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
12    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
13    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
14    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
15    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
16    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
17    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
18    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
19    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
20    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
21    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
22    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
23    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
24    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
25    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
26    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
27    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
28    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
29    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
...   ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   ...     ...     
1677  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1678  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1679  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1680  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1681  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1682  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1683  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1684  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1685  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1686  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1687  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1688  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1689  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1690  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1691  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1692  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1693  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1694  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1695  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1696  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1697  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1698  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   ...     0.0     
1699  0.0  0

In [98]:
pd.set_option('display.max_colwidth', -1)

In [325]:
# second_layer
tfidf_all_text[tfidf_all_text['cluster']==0]['item_name']

0       4-or-12-pack: Inkworks Projector Pens                                         
1       Pacific Pearls 3-Piece Pendant, Ring, and Earrings Gift Set                   
2       Pick 4: Angry Mills Protein-Infused Caffeinated Nut Spreads                   
3       NOTILUS Antimicrobial 3-in-1 Rain Shower Spa Combo                            
4       2-for-Tuesday: Bogui Wallets with or without RFID Cards                       
5       Polk Nue Era Headphones                                                       
6       ☕ The Process Shirt And/Or ☕ The Dream Shirt                                  
7       Grilling Traditions 3-Piece Pizza Stone Set                                   
8       18K Gold-Plated Heart Pendant with Diamond (1 Sapphire OR 1 Sapphire & 1 Ruby)
9       Primula Cold Brew Coffee Maker with 2 Travel Brewers                          
11      2-for-Tuesday: Power Precision Sous Vide with Bonus Cooking Rack              
12      Rowkin Bit Charge Stereo Bluetooth 

In [326]:
# unlucky 
tfidf_all_text[tfidf_all_text['cluster']==1]['item_name']

129    Fukobukuro Shirt & Empty Fukobukuro Bag
231    Fukobukuro 19: Fools Rush In           
232    Fukobukuro 19: Fools Rush In           
234    Fukobukuro 19: Fools Rush In           
235    Fukobukuro 19: Fools Rush In           
236    Fukobukuro 19: Fools Rush In           
237    Fukobukuro 19: Fools Rush In           
238    Fukobukuro 19: Fools Rush In           
239    Fukobukuro 19: Fools Rush In           
240    Fukobukuro 19: Fools Rush In           
241    Fukobukuro 19: Fools Rush In           
242    Fukobukuro 19: Fools Rush In           
243    Fukobukuro 19: Fools Rush In           
244    Fukobukuro 19: Fools Rush In           
245    Fukobukuro 19: Fools Rush In           
246    Fukobukuro 19: Fools Rush In           
247    Fukobukuro 19: Fools Rush In           
248    Fukobukuro 19: Fools Rush In           
249    Fukobukuro 19: Fools Rush In           
250    Fukobukuro 19: Fools Rush In           
251    Fukobukuro 19: Fools Rush In           
252    Fukobu

In [327]:
# knives
tfidf_all_text[tfidf_all_text['cluster']==2]['item_name']

76      2-Pack: C.R.K.T. Ruger Go-N-Heavy Compact VEFF Serrated Knives              
167     Kai Inspire 5-Piece Cutlery Set                                             
348     Good / Better / Best Cutlery                                                
595     Kai Luna 6-Piece Knife Set                                                  
614     A Few Pounds Of Melted Candy Corn And A Knife                               
657     Quikut 20-Piece Knife Set                                                   
678     GoPro Hero4 Session HD 1080P Action Camera                                  
679     12oz Meh Tumbler                                                            
680     Minx NY Socks for the Fam (Men's, Women's & Kids)                           
681     2-Pack: Ivy USB Port LED Desk Lamps                                         
682     SteelSeries Arctis 3 Universal Gaming Headset (Refurbished)                 
683     10-Pack Random UV-Protected Sunglasses                   

In [328]:
# portable speakers
tfidf_all_text[tfidf_all_text['cluster']==3]['item_name']

125     Speaker Dock, um, Sunday?: Hale Speaker Dock                                    
228     2-for-Tuesday: ION Audio Sound Shine Lightbulb Speakers                         
400     iHome Kineta K1 Portable Bluetooth Speaker & Power Bank                         
502     Sphereo True Wireless Stereo Bluetooth Speakers with Charging Base              
616     Bem Ohana 3-Piece Indoor/Outdoor Bluetooth Audio System                         
702     Gabba Goods Bluetooth Wireless Eye Masks                                        
703     2-Pack: Mini Compact "Travel Massager"                                          
726     mPulse Rock Bluetooth On-Ear Headphones                                         
734     QFX Elite Series WiFi+Bluetooth Speakers                                        
761     Onkyo 5.1.2-Channel Dolby Atmos Speaker System                                  
764     2-for-Tuesday: QFX E-200 Portable WiFi + Bluetooth Multi-Room Speakers          
769     mPULSE Blast 

In [329]:
# speakers
tfidf_all_text[tfidf_all_text['cluster']==4]['item_name']

10      Portable Echo Dot Speaker Dock with Power Bank                                
43      Envic Unlocked Android Phone & Smartwatch Bundle                              
58      Rowkin Bit Stereo True Wireless Bluetooth Earbuds                             
123     2-for-Tuesday: Bauhn Sweatproof  Bluetooth Sport Headphones with Case         
127     Zen Logic Wireless Speaker/Power Bank Bundles                                 
148     Martian Mvoice Smartwatch with Alexa                                          
160     Batband Ear-Free Wireless Hearable                                            
190     Braven XXL Portable Outdoor Bluetooth Speaker (Refurbished)                   
305     Freshebuds Air Magnetic Bluetooth Earbuds                                     
306     Win Them Back Bundle                                                          
315     Braven BRV-1M Ultra-Rugged IPX7 Bluetooth Speaker                             
324     10-or-20-for-Tuesday: Fidget Spinne

In [330]:
silhouette_avg = silhouette_score(transformed_text, tfidf_all_text['cluster'])
silhouette_avg

0.6786572810111529

In [331]:
data['first_layer_label'] = tfidf_all_text['cluster']

In [332]:
data

datetime  \
0    2018-11-17 05:00:07.557   
1    2018-11-16 05:00:07.922   
2    2018-11-15 05:00:04.026   
3    2018-11-14 05:00:08.839   
4    2018-11-13 05:00:00.503   
5    2018-11-12 05:00:06.036   
6    2018-11-11 05:00:03.094   
7    2018-11-10 05:00:31.466   
8    2018-11-09 05:00:01.032   
9    2018-11-08 05:00:04.026   
10   2018-11-07 05:00:06.482   
11   2018-11-06 05:00:05.999   
12   2018-11-05 05:00:09.745   
13   2018-11-04 04:00:05.099   
14   2018-11-03 04:00:03.903   
15   2018-11-02 04:00:05.893   
16   2018-11-01 04:00:05.247   
17   2018-10-31 04:00:04.899   
18   2018-10-30 04:00:07.136   
19   2018-10-29 04:00:09.519   
20   2018-10-28 04:00:02.109   
21   2018-10-27 04:00:12.340   
22   2018-10-26 04:00:03.801   
23   2018-10-25 04:00:09.038   
24   2018-10-24 04:00:06.142   
25   2018-10-23 04:00:01.475   
26   2018-10-22 04:00:03.164   
27   2018-10-21 04:00:03.298   
28   2018-10-20 04:00:46.966   
29   2018-10-19 04:00:01.945   
...                      ...   
1677 2014-08-28 04:00:01.265   
1678 2014-08-27 04:00:01.374   
1679 2014-08-26 04:00:01.851   
1680 2014-08-25 03:59:59.499   
1681 2014-08-24 04:00:00.802   
1682 2014-08-22 04:00:01.984   
1683 2014-08-21 04:00:01.538   
1684 2014-08-20 04:00:01.535   
1685 2014-08-19 04:00:01.270   
1686 2014-08-18 04:00:01.321   
1687 2014-08-15 04:00:01.425   
1688 2014-08-14 04:00:00.465   
1689 2014-08-13 04:00:00.662   
1690 2014-08-12 04:00:00.501   
1691 2014-08-11 04:00:00.316   
1692 2014-08-10 04:00:00.304   
1693 2014-08-09 04:00:00.764   
1694 2014-08-08 04:00:00.509   
1695 2014-08-04 04:00:01.393   
1696 2014-07-30 04:00:01.171   
1697 2014-07-28 04:00:00.962   
1698 2014-07-27 04:00:01.241   
1699 2014-07-26 04:00:01.229   
1700 2014-07-24 04:00:01.717   
1701 2014-07-19 04:00:01.879   
1702 2014-07-16 04:00:01.117   
1703 2014-07-15 04:00:00.693   
1704 2014-07-14 04:00:01.287   
1705 2014-07-10 04:00:01.199   
1706 2014-07-09 04:00:00.704   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              item_features  \
0     These are pens that can project designs out of their butts.\nYou can get 4 of same kind for $10, or all 12 different ones for $20.\nIt feels like forever since I’ve had to write about a projector. It’s good to be back, baby.\nModel numbers: 1INKIW4116-00, 1INKIW4142-00, 1INKIW4154-00, 1INKIW4134-00, 1INKIW4150-00, ST1NKYF4RT-00, 1INKIW4143-00, 1INKIW4157-00, 1INKIW4144-00, 1INKIW4136-00, 1INKIW4152-00, 1INKIW4149-00, 1INKIW4110-00. Now, let’s play a round of spot the fake model number!                                                                                                                                                                                                                                                                                                              
1     You get a pendant, a set of earrings, and a ring to match.\nThis holiday season, get that special someone something creative, something that’ll blow their mind on Christmas morning…\nOr get them this.\nHonestly, it’s way less risky.\nModel: BOR458M, BOR471M, BOR595M, BOR629M, BOR863M. And they each include a ring. But they’re anything but BOR-ring.                                                                                 

In [333]:
layer2 = data[data['first_layer_label']== 0]

# layer2 dimention reduction to 2 principal components, 6 cluster, best for layer2

In [334]:
layer2

datetime  \
0    2018-11-17 05:00:07.557   
1    2018-11-16 05:00:07.922   
2    2018-11-15 05:00:04.026   
3    2018-11-14 05:00:08.839   
4    2018-11-13 05:00:00.503   
5    2018-11-12 05:00:06.036   
6    2018-11-11 05:00:03.094   
7    2018-11-10 05:00:31.466   
8    2018-11-09 05:00:01.032   
9    2018-11-08 05:00:04.026   
11   2018-11-06 05:00:05.999   
12   2018-11-05 05:00:09.745   
13   2018-11-04 04:00:05.099   
14   2018-11-03 04:00:03.903   
15   2018-11-02 04:00:05.893   
16   2018-11-01 04:00:05.247   
17   2018-10-31 04:00:04.899   
18   2018-10-30 04:00:07.136   
19   2018-10-29 04:00:09.519   
20   2018-10-28 04:00:02.109   
21   2018-10-27 04:00:12.340   
22   2018-10-26 04:00:03.801   
23   2018-10-25 04:00:09.038   
24   2018-10-24 04:00:06.142   
25   2018-10-23 04:00:01.475   
26   2018-10-22 04:00:03.164   
27   2018-10-21 04:00:03.298   
28   2018-10-20 04:00:46.966   
29   2018-10-19 04:00:01.945   
30   2018-10-18 04:00:28.370   
...                      ...   
1668 2014-09-18 04:00:02.371   
1669 2014-09-16 04:00:02.061   
1670 2014-09-10 04:00:01.816   
1671 2014-09-06 04:00:01.629   
1672 2014-09-04 04:00:01.321   
1674 2014-09-01 04:00:01.794   
1675 2014-08-30 04:00:00.757   
1676 2014-08-29 04:00:01.435   
1677 2014-08-28 04:00:01.265   
1678 2014-08-27 04:00:01.374   
1679 2014-08-26 04:00:01.851   
1682 2014-08-22 04:00:01.984   
1684 2014-08-20 04:00:01.535   
1685 2014-08-19 04:00:01.270   
1686 2014-08-18 04:00:01.321   
1689 2014-08-13 04:00:00.662   
1690 2014-08-12 04:00:00.501   
1691 2014-08-11 04:00:00.316   
1693 2014-08-09 04:00:00.764   
1695 2014-08-04 04:00:01.393   
1696 2014-07-30 04:00:01.171   
1697 2014-07-28 04:00:00.962   
1698 2014-07-27 04:00:01.241   
1699 2014-07-26 04:00:01.229   
1700 2014-07-24 04:00:01.717   
1701 2014-07-19 04:00:01.879   
1702 2014-07-16 04:00:01.117   
1703 2014-07-15 04:00:00.693   
1705 2014-07-10 04:00:01.199   
1706 2014-07-09 04:00:00.704   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              item_features  \
0     These are pens that can project designs out of their butts.\nYou can get 4 of same kind for $10, or all 12 different ones for $20.\nIt feels like forever since I’ve had to write about a projector. It’s good to be back, baby.\nModel numbers: 1INKIW4116-00, 1INKIW4142-00, 1INKIW4154-00, 1INKIW4134-00, 1INKIW4150-00, ST1NKYF4RT-00, 1INKIW4143-00, 1INKIW4157-00, 1INKIW4144-00, 1INKIW4136-00, 1INKIW4152-00, 1INKIW4149-00, 1INKIW4110-00. Now, let’s play a round of spot the fake model number!                                                                                                                                                                                                                                                                                                              
1     You get a pendant, a set of earrings, and a ring to match.\nThis holiday season, get that special someone something creative, something that’ll blow their mind on Christmas morning…\nOr get them this.\nHonestly, it’s way less risky.\nModel: BOR458M, BOR471M, BOR595M, BOR629M, BOR863M. And they each include a ring. But they’re anything but BOR-ring.                                                                                 

In [335]:
layer2_tfidf_dscrp = nlp.tfidf_content(layer2['descriptions']).set_index(layer2.index)

In [336]:
layer2_tfidf_dscrp

0    1    2    3    4    5    6    7    8    9  ...    11126  11127  \
0     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
2     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
3     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
4     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
5     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
6     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
7     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
8     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
9     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
11    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
12    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
13    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
14    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
15    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
16    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
17    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
18    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
19    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
20    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
21    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
22    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
23    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
24    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
25    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
26    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
27    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
28    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
29    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
30    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
...   ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...    ...    ...     
1668  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1669  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1670  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1671  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1674  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1675  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1676  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1677  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1678  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1679  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1682  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1684  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1685  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1686  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1689  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1690  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1691  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0    0.0     
1693  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ..

In [362]:
layer2_pca_2 = PCA(2)
layer2_pca_3 = PCA(3)
layer2_pca = layer2_pca_2.fit_transform(layer2_tfidf_dscrp)

In [363]:
layer2_kmeans = KMeans(n_clusters=5)
layer2_kmeans.fit(layer2_pca)
layer2['second_layer_cluster'] = layer2_kmeans.labels_

/Users/boyueshen/anaconda3/lib/python3.5/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [339]:
layer2

datetime  \
0    2018-11-17 05:00:07.557   
1    2018-11-16 05:00:07.922   
2    2018-11-15 05:00:04.026   
3    2018-11-14 05:00:08.839   
4    2018-11-13 05:00:00.503   
5    2018-11-12 05:00:06.036   
6    2018-11-11 05:00:03.094   
7    2018-11-10 05:00:31.466   
8    2018-11-09 05:00:01.032   
9    2018-11-08 05:00:04.026   
11   2018-11-06 05:00:05.999   
12   2018-11-05 05:00:09.745   
13   2018-11-04 04:00:05.099   
14   2018-11-03 04:00:03.903   
15   2018-11-02 04:00:05.893   
16   2018-11-01 04:00:05.247   
17   2018-10-31 04:00:04.899   
18   2018-10-30 04:00:07.136   
19   2018-10-29 04:00:09.519   
20   2018-10-28 04:00:02.109   
21   2018-10-27 04:00:12.340   
22   2018-10-26 04:00:03.801   
23   2018-10-25 04:00:09.038   
24   2018-10-24 04:00:06.142   
25   2018-10-23 04:00:01.475   
26   2018-10-22 04:00:03.164   
27   2018-10-21 04:00:03.298   
28   2018-10-20 04:00:46.966   
29   2018-10-19 04:00:01.945   
30   2018-10-18 04:00:28.370   
...                      ...   
1668 2014-09-18 04:00:02.371   
1669 2014-09-16 04:00:02.061   
1670 2014-09-10 04:00:01.816   
1671 2014-09-06 04:00:01.629   
1672 2014-09-04 04:00:01.321   
1674 2014-09-01 04:00:01.794   
1675 2014-08-30 04:00:00.757   
1676 2014-08-29 04:00:01.435   
1677 2014-08-28 04:00:01.265   
1678 2014-08-27 04:00:01.374   
1679 2014-08-26 04:00:01.851   
1682 2014-08-22 04:00:01.984   
1684 2014-08-20 04:00:01.535   
1685 2014-08-19 04:00:01.270   
1686 2014-08-18 04:00:01.321   
1689 2014-08-13 04:00:00.662   
1690 2014-08-12 04:00:00.501   
1691 2014-08-11 04:00:00.316   
1693 2014-08-09 04:00:00.764   
1695 2014-08-04 04:00:01.393   
1696 2014-07-30 04:00:01.171   
1697 2014-07-28 04:00:00.962   
1698 2014-07-27 04:00:01.241   
1699 2014-07-26 04:00:01.229   
1700 2014-07-24 04:00:01.717   
1701 2014-07-19 04:00:01.879   
1702 2014-07-16 04:00:01.117   
1703 2014-07-15 04:00:00.693   
1705 2014-07-10 04:00:01.199   
1706 2014-07-09 04:00:00.704   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              item_features  \
0     These are pens that can project designs out of their butts.\nYou can get 4 of same kind for $10, or all 12 different ones for $20.\nIt feels like forever since I’ve had to write about a projector. It’s good to be back, baby.\nModel numbers: 1INKIW4116-00, 1INKIW4142-00, 1INKIW4154-00, 1INKIW4134-00, 1INKIW4150-00, ST1NKYF4RT-00, 1INKIW4143-00, 1INKIW4157-00, 1INKIW4144-00, 1INKIW4136-00, 1INKIW4152-00, 1INKIW4149-00, 1INKIW4110-00. Now, let’s play a round of spot the fake model number!                                                                                                                                                                                                                                                                                                              
1     You get a pendant, a set of earrings, and a ring to match.\nThis holiday season, get that special someone something creative, something that’ll blow their mind on Christmas morning…\nOr get them this.\nHonestly, it’s way less risky.\nModel: BOR458M, BOR471M, BOR595M, BOR629M, BOR863M. And they each include a ring. But they’re anything but BOR-ring.                                                                                 

In [364]:
# 2 principal, 5 cluster score 0.4261
silhouette_avg = silhouette_score(layer2_pca, layer2_kmeans.labels_)
silhouette_avg

0.4260840068134142

In [365]:
# technology/smart devices
layer2[layer2['second_layer_cluster']==0]['item_name']

12      Rowkin Bit Charge Stereo Bluetooth Earbuds                                     
17      Pure Enrichment Hume Ultrasonic Cool Mist Humidifier                           
31      15-channel 1:14 scale R/C Excavator with Metal Shovel                          
33      HP 14" Chromebook (Refurbished)                                                
39      5-for-Tuesday: SmartStand Compact Phone & Tablet Stands                        
57      LG 1000W RMS Hi-Fi Entertainment & Karaoke System                              
59      KeySmart Aluminum with Expansion Pack Or KeySmart Pro with Tile                
62      The "Boo, Summer Is Over" Bundle                                               
67      2-for-Tuesday: Adrienne Vittadini Charging Wallets with RFID Protection        
79      PureGlow Crystal 2-in-1 Himalayan Salt Lamp & Ultrasonic Essential Oil Diffuser
90      5-Pack: Smart Stand Compact Phone & Tablet Stands                              
91      2-Pack or 10-Pack: Xsori

In [366]:
# powerbank/light
layer2[layer2['second_layer_cluster']==1]['item_name']

26      160-Pack Fidget Spinners                                                  
30      6-Pack: Pop Lights Halloween Treat Bags with LED Lights                   
42      Xsories Sneaker Power Bank and Dual USB Charger                           
47      40-pack or 160-Pack: Fidget Spinners                                      
50      GoWise Ultimate Flashlight Bundle                                         
68      iJoy 10,000 mAh Jump Starter Kit                                          
74      4-Pack: Portable Solar & Hand Crank LED Flashlight/Lanterns               
108     Cyntur JumperPack Mini Lithium-Ion Jumpstarter                            
109     4-for-Tuesday: 6-Outlet Surge Protectors with 2 USB Ports and Anchor Screw
120     96 or 192-Pack: Eveready AA SHD Batteries                                 
122     Yukon Outfitters Defender 1000-Lumen Flashlight                           
151     4-for-Tuesday: Xsories 9,000mAh Sneaker Power Bank                        
161 

In [367]:
# camera/drone
layer2[layer2['second_layer_cluster']==2]['item_name']

28      Hobbico Flitt Selfie Drone                                           
35      Odyssey Stellar NX Drone Bundle with Mini Drone and VR Headset       
38      Pogocam Wearable HD Camera with Pogotrack Sunglasses                 
51      360FLY 360-Degree HD Action Camera                                   
54      3-Pack: Lynx 1080p Security Cameras with Facial Recognition          
60      2-for-Tuesday: Zmodo MeShare 720P Wifi Cameras                       
81      2-for-Tuesday: Motorola 1080P Wifi Cameras with Smart Tag            
99      Canon EOS Rebel T6i Bundle                                           
114     Odyssey Stellar NX Drone Bundle with Mini Drone and VR Headset       
178     Zmodo Pivot 1080p 360° WiFi Camera with Smarthub and Window Sensors  
181     ALC Connect Home and Office Security System                          
208     WASPcam ROX Series 4K Action Camera                                  
218     Zmodo Pivot 1080p 360° WiFi Camera with Smarthub and Win

In [368]:
layer2[layer2['second_layer_cluster']==3]['item_name']

6       ☕ The Process Shirt And/Or ☕ The Dream Shirt                                  
9       Primula Cold Brew Coffee Maker with 2 Travel Brewers                          
13      6-Pack: 50"x60" Fleece Blankets With Or Without Meh Logo                      
20      Free Hugs Shirt by ApeLad                                                     
32      4-or-24-for-Tuesday: 50"x60" Fleece Blankets                                  
34      Meh Cat Shirt: Loafing or Loathing?                                           
41      Faces of Meh Shirt                                                            
44      5-Pack: EuroSock Premium Athletic Socks                                       
48      Stealth Meh or Stealth Mediocre Shirt                                         
52      Unsimply Stitched 3-Pack Socks                                                
55      42-Pack Gift Bags                                                             
69      Pacific Pearl Treasure Island Gemst

In [369]:
layer2[layer2['second_layer_cluster']==4]['item_name']

0       4-or-12-pack: Inkworks Projector Pens                                         
1       Pacific Pearls 3-Piece Pendant, Ring, and Earrings Gift Set                   
2       Pick 4: Angry Mills Protein-Infused Caffeinated Nut Spreads                   
3       NOTILUS Antimicrobial 3-in-1 Rain Shower Spa Combo                            
4       2-for-Tuesday: Bogui Wallets with or without RFID Cards                       
5       Polk Nue Era Headphones                                                       
7       Grilling Traditions 3-Piece Pizza Stone Set                                   
8       18K Gold-Plated Heart Pendant with Diamond (1 Sapphire OR 1 Sapphire & 1 Ruby)
11      2-for-Tuesday: Power Precision Sous Vide with Bonus Cooking Rack              
14      3-Pack: Model Technics Metal Puzzles                                          
15      CBD Gummy Bears (Regular or Sour)                                             
16      Lovesac Sactionals for Kids & Pets 

In [370]:
data['second_layer_label']=layer2['second_layer_cluster']

In [371]:
data_train

datetime  \
366  2018-01-09 05:00:09.261   
1039 2016-07-09 04:00:03.618   
634  2017-08-06 04:00:05.182   
984  2016-09-03 04:00:02.239   
524  2017-09-27 04:00:01.038   
955  2016-10-02 04:00:00.000   
663  2017-07-11 03:00:00.279   
1374 2015-08-05 04:00:00.992   
1633 2014-11-07 05:00:08.785   
68   2018-09-10 04:00:07.582   
1363 2015-08-16 04:00:02.066   
325  2018-02-19 05:00:11.738   
1436 2015-06-04 04:00:00.429   
1636 2014-11-03 05:00:01.247   
1261 2015-11-29 05:00:01.228   
1273 2015-11-17 05:00:01.362   
830  2017-03-17 04:00:14.221   
1291 2015-10-29 04:00:03.774   
17   2018-10-31 04:00:04.899   
586  2017-09-19 03:30:02.818   
1589 2014-12-30 05:00:06.081   
930  2016-10-27 04:00:13.858   
51   2018-09-27 04:00:08.000   
1185 2016-02-13 05:00:00.641   
1135 2016-04-03 04:00:01.090   
1057 2016-06-21 04:00:04.413   
1422 2015-06-18 04:00:02.541   
270  2018-04-02 03:40:03.824   
1667 2014-09-19 04:00:01.841   
1157 2016-03-12 05:00:01.851   
...                      ...   
65   2018-09-13 04:00:05.184   
90   2018-08-19 04:00:02.021   
1094 2016-05-15 04:00:02.791   
253  2018-04-02 03:40:03.824   
102  2018-08-07 04:00:06.333   
1233 2015-12-27 05:00:00.752   
550  2017-09-19 03:30:02.818   
133  2018-07-07 04:00:00.470   
1462 2015-05-09 04:00:00.797   
3    2018-11-14 05:00:08.839   
299  2018-03-17 04:00:14.405   
836  2017-03-11 05:00:05.484   
471  2017-11-19 05:00:08.278   
532  2017-09-19 04:01:26.151   
101  2018-08-08 04:00:06.259   
1154 2016-03-15 04:00:00.424   
1256 2015-12-04 05:00:02.452   
1546 2015-02-11 05:00:00.203   
1558 2015-01-30 05:00:01.115   
215  2018-04-16 04:00:10.963   
148  2018-06-22 04:00:04.254   
1347 2015-09-02 04:00:02.923   
1434 2015-06-06 04:00:00.403   
91   2018-08-18 04:00:05.333   
700  2017-07-11 03:00:00.279   
641  2017-07-30 04:00:02.365   
906  2016-11-20 05:00:13.904   
742  2017-06-14 04:00:03.784   
740  2017-06-16 04:00:09.723   
1207 2016-01-22 05:00:00.509   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        item_features  \
366   You get 2 kendama/yo-yo combos for the price of about 1/2 a normal kendama\nFor the uninitiated, kendamas are a Japanese toy that is sweeping America’s youth culture like so many Pokemon or Tamagotchi\nThese are made by Duncan, the classic toy manufacturer, who couldn’t help but turn it into a yo-yo\nThe perfect Valentine’s gift if you are an idiot\nModel: 3860KE (Although our hope for America’s future fades by the day, it’s good to see that our children are being exposed to high-quality model numbers at an early age)                                                                                                                                                                                                                                                                                                                                                                                                       
1039  Do not eat no matter how delicious it looks\nMark the momentous occasion of our second birthday\nNo, seriously, we need a reminder because by this time next year we’ll be like “I dunno, w

# layer2 dimention reduction to 2 principal components, not as good

In [194]:
# pca2 = PCA(2)
# layer2_pca2 = pca2.fit_transform(layer2_tfidf_dscrp.drop(columns='cluster'))
layer2_kmeans = KMeans(n_clusters=5)
layer2_kmeans.fit(layer2_pca2)
layer2_tfidf_dscrp['cluster'] = layer2_kmeans.labels_

In [195]:
silhouette_avg = silhouette_score(layer2_pca2, layer2_tfidf_dscrp['cluster'])
silhouette_avg

0.40947410192446326

In [196]:
layer2_tfidf_dscrp.groupby('cluster').groups[0]

Index(['Grime Boss Hand Wipes 8-Pack',
       '2-for-Tuesday: Duncan Groove Yo-yo Kendama', 'Targus Laptop Bag',
       'Nespresso Vertuo Espresso & Coffee Machine with Milk Frother (Refurbished)',
       'FoodSaver V3230 Vacuum Sealing System (Refurbished)',
       'Red Rock Canyon 45L Backpack', 'Targus Drifter II 17" Laptop Backpack',
       'Nutri Ninja Pro BL450 (Refurbished)',
       'Cool Gear 10-Piece Food Storage Bundle',
       'Fukobukuro 12: Morning Addition',
       ...
       'Star Wars Bundle', 'Weston Deluxe Heavy Duty #32 Meat Grinder',
       'Solo Active Laptop Backpack',
       '2-for-Tuesday: ProSupps Crash Sleep-Aid (60 servings)',
       'Ashen Crossbody Bags by Parinda Handbags',
       'Alpine Design Backpacks and Random Color Hydration Pack',
       'iEnjoy Down & Feather Pillows',
       'Meh's 4th Birthday: The Final Fukobukuro',
       '2-for-Tuesday: BioBidet BBC-70 Bidets', 'Fūl Apex Laptop Backpack'],
      dtype='object', name='item_name', length=615)

In [197]:
layer2_tfidf_dscrp.groupby('cluster').groups[1]

Index(['20-Pack: Random Fidget Spinners',
       '2-Pack: Dorcy Pro Series AC/DC Rechargeable Portable Work Light',
       '2-for-Tuesday: Eveready Compact LED Area Lights',
       '3-Pack: 6" Fluorescent Lights',
       'Eveready Gold AA Alkaline Batteries (72-Pack)',
       '2-for-Tuesday: Mighty Charger Disposable Battery Chargers',
       '2-for-Tuesday: Rechargeable 5-in-1 Emergency Tools',
       'Toshiba AA Alkaline Batteries (40-Pack)',
       '36 or 96 Pack: Energizer EcoAdvanced AA Batteries',
       'GreenTech Pure Power Dimmable LED Light Bulbs (6-Pack)',
       '2-for-Tuesday: Readymax Pliers with LED Light',
       'Life Gear Auto Emergency Tool LED Flashlight',
       '2-for-Tuesday: Bluetech Emergency LED Flashlights with Motion Detection',
       'American Lighting LED Rope/Tape Hybrid Lights',
       'Westek 16" Dimmable LED Light Bar',
       '3-Pack: Multi-Function LED Lantern Lights',
       'American Lighting LED Rope/Tape Hybrid Lights',
       'Yukon Outfitters 

In [198]:
layer2_tfidf_dscrp.groupby('cluster').groups[2]

Index(['4-Pack: 2 Meh Pillows, 1 Meh Tumbler & 1 Random Shirt',
       'Birthday Meh Shirt on American Apparel',
       'Fukobukuro 17: Meh-rathon Edition',
       'Meh Shirts, Get Your Meh Shirts Here',
       'Fukobukuro 18: Meh-rathon Edition', 'Meh Pixel Shirt',
       '3-Pack: FootCardigan Socks',
       '3-Pack: Unsimply Stitched Men's Dress Socks', '12-Pack: Women's Socks',
       'Free Hugs Shirt by ApeLad',
       'Meh: Year One Limited Edition Commemorative Collectors Shirt',
       '6-Pack: 50"x60" Fleece Blankets With Or Without Meh Logo',
       'Fukobukuro 18: Meh-rathon Edition',
       'Stealth Meh or Stealth Mediocre Shirt',
       'Meh Shirt on American Apparel',
       'Almost Blank Meh American Apparel Shirt',
       'Meh Shirt with Frosting and Sprinkles',
       'Meh Cat Shirt: Loafing or Loathing?', 'Saturday Slob Kit',
       '3-Pack: Unsimply Stitched Socks', 'Meh Shirt',
       '6-Pack: Men's Funky Socks', 'Unsimply Stitched 3-Pack Socks',
       '3-Pack: Unsi

In [199]:
layer2_tfidf_dscrp.groupby('cluster').groups[3]

Index(['Bem Bravo Bluetooth Speaker',
       'Quirky Pivot Power Surge Protector Bundle (Random-Colored 4-Outlet & 6-Outlet)',
       'Olio Model One Smartwatch (Refurbished)',
       'Seiki 50" 1080p LED Smart TV',
       'PurePedi 8-in-1 Manicure and Pedicure Kit',
       '2-for-Tuesday: Bracketron Twist and Charge USB Chargers',
       'Zipstick 2200mAh Rechargeable Power Bank',
       'KeySmart Aluminum with Expansion Pack Or KeySmart Pro with Tile',
       'Duracell 8800mAh & 1850mAh Power Bank Set with or without Powermat',
       '2-for-Tuesday: Oregon Scientific Digital Emergency Alert Radios',
       ...
       '2-Pack: Merkury Color LED WiFi Bulbs',
       'Acer Aspire Switch 11.6" 4GB RAM, 128GB SSD Tablet PC (Refurbished)',
       'Saturday Toy Bundle', 'AOC IPS LED Frameless Monitor (Refurbished)',
       'PCH Digital Pulse Massager',
       'Little Giant Go-2 13' Multipurpose Ladder',
       'Toshiba 13.3" Chromebook 2 (Refurbished)',
       '2-for-Tuesday: Power Style CR

In [200]:
layer2_tfidf_dscrp.groupby('cluster').groups[4]

Index(['MOTA JetJat Ultra FPV Drone',
       'Pronto and Peel Smart Universal Remote Control',
       'Cheerson Mini Quadcopter Selection', 'Cheerson CX-10 Mini Quadcopter',
       'GoPro Hero4 Session HD 1080P Action Camera',
       '2-for-Tuesday: Stem Izon View Wi-Fi Video Monitors',
       'SJ230 Mid-Size Helicopter or Cheerson CX-10 Quadcopter',
       'HP Pavilion 500-217C Desktop PC (Refurbished)',
       'Razer Carcharias Gaming Headphones and Mic (Refurbished)',
       'Foscam Wireless IP Camera 720p (Refurbished)',
       ...
       '2-for-Tuesday: 39" Emerson 1080p TV's (Refurbished)',
       'Stem Izon 2.0 Wi-Fi Video Monitor', 'BIOS Bullet Action Cam Selection',
       'Foscam Outdoor Wireless IP Camera (Refurbished)',
       'HP 14" Stream Laptop PC (Refurbished)',
       '2-for-Tuesday: Stem Izon View Wi-Fi Video Monitors',
       'Papago LORA 381 1080p Dash Cam (Recertified)',
       'HP Titan JUXT Smartwatch', 'Powerbeats2 Wireless Headphones',
       'Foscam Pan/Tilt 

In [379]:
layer3 = data[(data['second_layer_label']== 3) | (data['second_layer_label']==4)]

# layer 3 clustering using only item_name

In [380]:
layer3_nlp_names = nlp.nlp_content(layer3['item_name'])

In [381]:
name_vec = nlp.tfidf_content(layer3_nlp_names).set_index(layer3.index)

In [382]:
name_vec

0    1    2    3    4    5    6    7         8         9  ...   1438  \
0     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
2     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
3     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
4     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
5     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
6     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
7     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
8     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.315285  ...   0.0    
9     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
11    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
13    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
14    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
15    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
16    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
18    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
19    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
20    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
21    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
22    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
23    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
24    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
25    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
27    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
29    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
32    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
34    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
36    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
37    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
40    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
...   ...  ...  ...  ...  ...  ...  ...  ...       ...       ...  ...   ...    
1632  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1637  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1639  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1642  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1645  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1648  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1650  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1654  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1655  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.499508  0.000000  ...   0.0    
1656  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1657  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1660  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1662  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1663  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1669  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1674  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1676  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000000  ...   0.0    
1682  0.

In [395]:
layer3_pca_2=PCA(2)
layer3_pca_3=PCA(3)
layer3_name_pca = layer3_pca_3.fit_transform(name_vec)

In [396]:
len(layer3_name_pca)

852

In [402]:
layer3_kmeans = KMeans(n_clusters=5)
layer3_kmeans.fit(layer3_name_pca)
layer3['cluster'] = layer3_kmeans.labels_

/Users/boyueshen/anaconda3/lib/python3.5/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [403]:
# layer3 only name 2 principle, 3 clusters
silhouette_avg = silhouette_score(layer3_name_pca, layer3['cluster'])
silhouette_avg

0.5879797605828055

In [404]:
layer3[layer3['cluster']==0]['item_name']

1       Pacific Pearls 3-Piece Pendant, Ring, and Earrings Gift Set                    
7       Grilling Traditions 3-Piece Pizza Stone Set                                    
53      2-for-Tuesday: Compact 121-Piece First Aid Medical Kit                         
69      Pacific Pearl Treasure Island Gemstone and Pearl Necklace & Bracelet Set       
85      Copper Cook 8-Piece Nonstick Copper Pan Set                                    
100     ProCabello 5-Piece Straightener and Styler Set with Shine and Hold Spray       
103     Pacific Pearls Genuine Mother of Pearl Double-Strand Necklace                  
119     The ¯\_(ツ)_/¯  Bundle                                                          
146     Copper Cook 6-in-1 Pan Set                                                     
158     2-for-Tuesday: Cotton Touch Microfiber Sheet Sets                              
199     Pacific Pearls 5-in-1 Gemstone & Pearl Lariat                                  
200     2-for-Tuesday: Cotton To

In [405]:
layer3[layer3['cluster']==1]['item_name']

34      Meh Cat Shirt: Loafing or Loathing?                         
41      Faces of Meh Shirt                                          
131     Meh's 4th Birthday: The Final Fukobukuro                    
132     4-Pack: 2 Meh Pillows, 1 Meh Tumbler & 1 Random Shirt       
230     Meh's Fuko Shirt                                            
286     Meh Face Pillows                                            
381     Meh Face Pillows                                            
402     Meh Shirt                                                   
403     Fukobukuro 18: Meh-rathon Edition                           
410     Fukobukuro 18: Meh-rathon Edition                           
418     Fukobukuro 18: Meh-rathon Edition                           
436     Fukobukuro 18: Meh-rathon Edition                           
451     Fukobukuro 18: Meh-rathon Edition                           
467     Meh Pixel Shirt                                             
533     Fukobukuro: Meh-rathon Edi

In [406]:
layer3[layer3['cluster']==2]['item_name']

366     2-for-Tuesday: Duncan Groove Yo-yo Kendama                             
1039    Meh Shirt with Frosting and Sprinkles                                  
1363    Pursonic S20 UV Family Toothbrush Sanitizer w/ AC Adapter              
1057    2-for-Tuesday: Pure Copper Moscow Mule Mugs                            
354     2-Pack: Happeseat® Carseat Covers                                      
177     2-Pack: Memory Foam Knee Pillow                                        
1368    2-for-Tuesday: InSite Locator and Transmitter                          
116     2-for-Tuesday: Bamboo Memory Foam Travel Pillows                       
25      4-for-Tuesday: Hudson & Mane Hair Fiber Bundles                        
431     Ashen Crossbody Bags by Parinda Handbags                               
1594    Cool Gear Stay Fit 3-Piece Set                                         
4       2-for-Tuesday: Bogui Wallets with or without RFID Cards                
39      5-for-Tuesday: SmartStand Compac

In [408]:
layer3[layer3['cluster']==3]['item_name']

29      iRobot Roomba 650 Robotic Vacuum (Refurbished)                              
65      FoodSaver Vacuum Sealing System with Starter Kit (Refurbished)              
96      iRobot Roomba 805 Vacuum Cleaning Robot (Refurbished)                       
107     FoodSaver FM2000 Vacuum Sealing System with Starter Kit (Refurbished)       
133     Winix 4-Stage True HEPA Air Cleaner (Refurbished)                           
136     Nespresso Vertuo Espresso & Coffee Machine (Refurbished)                    
142     FoodSaver V3230 Vacuum Sealing System (Refurbished)                         
180     Shark Duo Clean Lift-Away Vacuum with Powered Head                          
202     Shark 2-in-1 Blast & Scrub Steam Pocket Mop (Refurbished)                   
309     Dyson V8 Animal Cord-Free Vacuum                                            
343     Shark Rocket DeluxePro Convertible Stick Vacuum                             
367     Shark Rocket TruePet Convertible Corded Vacuum           

In [409]:
layer3[layer3['cluster']==4]['item_name']

2       Pick 4: Angry Mills Protein-Infused Caffeinated Nut Spreads                     
3       NOTILUS Antimicrobial 3-in-1 Rain Shower Spa Combo                              
4       2-for-Tuesday: Bogui Wallets with or without RFID Cards                         
5       Polk Nue Era Headphones                                                         
6       ☕ The Process Shirt And/Or ☕ The Dream Shirt                                    
8       18K Gold-Plated Heart Pendant with Diamond (1 Sapphire OR 1 Sapphire & 1 Ruby)  
9       Primula Cold Brew Coffee Maker with 2 Travel Brewers                            
11      2-for-Tuesday: Power Precision Sous Vide with Bonus Cooking Rack                
15      CBD Gummy Bears (Regular or Sour)                                               
16      Lovesac Sactionals for Kids & Pets                                              
19      KitchenAid 3.5 Cup Food Chopper & Processor                                     
20      Free Hugs Shi

# layer 3 clustering using only description

In [410]:
layer3

datetime  \
0    2018-11-17 05:00:07.557   
1    2018-11-16 05:00:07.922   
2    2018-11-15 05:00:04.026   
3    2018-11-14 05:00:08.839   
4    2018-11-13 05:00:00.503   
5    2018-11-12 05:00:06.036   
6    2018-11-11 05:00:03.094   
7    2018-11-10 05:00:31.466   
8    2018-11-09 05:00:01.032   
9    2018-11-08 05:00:04.026   
11   2018-11-06 05:00:05.999   
13   2018-11-04 04:00:05.099   
14   2018-11-03 04:00:03.903   
15   2018-11-02 04:00:05.893   
16   2018-11-01 04:00:05.247   
18   2018-10-30 04:00:07.136   
19   2018-10-29 04:00:09.519   
20   2018-10-28 04:00:02.109   
21   2018-10-27 04:00:12.340   
22   2018-10-26 04:00:03.801   
23   2018-10-25 04:00:09.038   
24   2018-10-24 04:00:06.142   
25   2018-10-23 04:00:01.475   
27   2018-10-21 04:00:03.298   
29   2018-10-19 04:00:01.945   
32   2018-10-16 04:00:03.596   
34   2018-10-14 04:00:06.462   
36   2018-10-12 04:00:20.860   
37   2018-10-11 04:00:06.347   
40   2018-10-08 04:00:02.529   
...                      ...   
1632 2014-11-09 05:00:09.765   
1637 2014-11-02 04:00:00.470   
1639 2014-10-30 04:00:00.730   
1642 2014-10-26 04:00:00.853   
1645 2014-10-22 04:00:01.186   
1648 2014-10-18 04:00:01.263   
1650 2014-10-16 04:00:01.070   
1654 2014-10-09 04:00:01.631   
1655 2014-10-08 04:00:02.331   
1656 2014-10-07 04:00:01.588   
1657 2014-10-04 04:00:01.467   
1660 2014-09-30 04:00:07.559   
1662 2014-09-28 04:00:03.870   
1663 2014-09-26 04:00:05.681   
1669 2014-09-16 04:00:02.061   
1672 2014-09-04 04:00:01.321   
1674 2014-09-01 04:00:01.794   
1676 2014-08-29 04:00:01.435   
1682 2014-08-22 04:00:01.984   
1684 2014-08-20 04:00:01.535   
1685 2014-08-19 04:00:01.270   
1689 2014-08-13 04:00:00.662   
1690 2014-08-12 04:00:00.501   
1696 2014-07-30 04:00:01.171   
1698 2014-07-27 04:00:01.241   
1699 2014-07-26 04:00:01.229   
1700 2014-07-24 04:00:01.717   
1701 2014-07-19 04:00:01.879   
1705 2014-07-10 04:00:01.199   
1706 2014-07-09 04:00:00.704   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 item_features  \
0     These are pens that can project designs out of their butts.\nYou can get 4 of same kind for $10, or all 12 different ones for $20.\nIt feels like forever since I’ve had to write about a projector. It’s good to be back, baby.\nModel numbers: 1INKIW4116-00, 1INKIW4142-00, 1INKIW4154-00, 1INKIW4134-00, 1INKIW4150-00, ST1NKYF4RT-00, 1INKIW4143-00, 1INKIW4157-00, 1INKIW4144-00, 1INKIW4136-00, 1INKIW4152-00, 1INKIW4149-00, 1INKIW4110-00. Now, let’s play a round of spot the fake model number!                                                                                                                                                                                                                                                                                                 
1     You get a pendant, a set of earrings, and a ring to match.\nThis holiday season, get that special someone something creative, something that’ll blow their mind on Christmas morning…\nOr get them this.\nHonestly, it’s way less risky.\nModel: BOR458M, BOR471M, BOR595M, BOR629M, BOR863M. And they each include a ring. But they’re anything but BOR-ring.                                                                                                           

In [411]:
layer3_tfidf_desp = nlp.tfidf_content(layer3['descriptions'])

In [419]:
layer3_pca_desp = layer3_pca_3.fit_transform(layer3_tfidf_desp)
layer3_kmeans = KMeans(n_clusters=3)
layer3_kmeans.fit(layer3_pca_desp)
layer3['cluster'] = layer3_kmeans.labels_

/Users/boyueshen/anaconda3/lib/python3.5/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


In [420]:
silhouette_avg = silhouette_score(layer3_pca_desp, layer3['cluster'])
silhouette_avg

0.7096404926835556

In [421]:
layer3[layer3['cluster']==0]['item_name']

0       4-or-12-pack: Inkworks Projector Pens                                         
2       Pick 4: Angry Mills Protein-Infused Caffeinated Nut Spreads                   
3       NOTILUS Antimicrobial 3-in-1 Rain Shower Spa Combo                            
4       2-for-Tuesday: Bogui Wallets with or without RFID Cards                       
5       Polk Nue Era Headphones                                                       
6       ☕ The Process Shirt And/Or ☕ The Dream Shirt                                  
7       Grilling Traditions 3-Piece Pizza Stone Set                                   
8       18K Gold-Plated Heart Pendant with Diamond (1 Sapphire OR 1 Sapphire & 1 Ruby)
9       Primula Cold Brew Coffee Maker with 2 Travel Brewers                          
11      2-for-Tuesday: Power Precision Sous Vide with Bonus Cooking Rack              
13      6-Pack: 50"x60" Fleece Blankets With Or Without Meh Logo                      
14      3-Pack: Model Technics Metal Puzzle

In [422]:
layer3[layer3['cluster']==1]['item_name']

44      5-Pack: EuroSock Premium Athletic Socks                        
52      Unsimply Stitched 3-Pack Socks                                 
87      12-Pack: Zeke Men's Socks                                      
115     6-Pack: Men's Funky Socks                                      
184     3-Pack: Unsimply Stitched Socks                                
211     It's Glen! Custom Socks                                        
335     Unsimply Stitched 3-Pack Socks                                 
424     3-Pack: Unsimply Stitched Socks                                
535     Minx NY SOCK MANIA                                             
624     3-Pack Unsimply Stitched Socks                                 
749     Random Socks (5-Pack Men's or Women's, 12-Pack Boy's or Girl's)
784     12-Pack: Women's Socks                                         
796     3-Pack: FootCardigan Socks                                     
839     3-Pack: Unsimply Stitched Men's Dress Socks             

In [423]:
layer3[layer3['cluster']==2]['item_name']

1       Pacific Pearls 3-Piece Pendant, Ring, and Earrings Gift Set                    
69      Pacific Pearl Treasure Island Gemstone and Pearl Necklace & Bracelet Set       
103     Pacific Pearls Genuine Mother of Pearl Double-Strand Necklace                  
199     Pacific Pearls 5-in-1 Gemstone & Pearl Lariat                                  
206     Baroque Pearl Rhodium Silver Charm Bracelet                                    
346     Diamond Encrusted Eternal Heart-Shaped Pearl Pendant And/Or Earrings           
365     Pacific Pearls Necklace, Bracelet, and Earring Set                             
395     Pacific Pearls Rose Atoll Collection 14K Gold Filled Pearl & Swarovski Necklace
425     Imperial Pearl 36" Station Necklace                                            
461     Pacific Pearls Gemstone and Pearl Necklace & Bracelet Set                      
482     8-Pack: Bormioli Momenti Wine Glasses                                          
508     36" Imperial Pearl Stati

In [292]:
layer3[layer3['cluster']==3]['item_name']

1039    Meh Shirt with Frosting and Sprinkles                                    
1135    350 Thread Count Down Alternative Pillows (Set of 4)                     
177     2-Pack: Memory Foam Knee Pillow                                          
116     2-for-Tuesday: Bamboo Memory Foam Travel Pillows                         
1499    Fukobukuro: The Unlucky Bag                                              
1626    Meh Farm to Table Bundle: Apron, Knife, Roaster & Thermometer            
331     2-for-Tuesday: Meh Stadium Blankets                                      
860     Fukobukuro 14: Lover's Remorse                                           
806     2-for-Tuesday: iEnjoy Down Pillows (Standard or King)                    
927     Cardiff S-Series Premium 3-Wheel Skates (Refurbished)                    
27      Casemates Octopus Shirt                                                  
722     10-for-Tuesday: Schick Hydro 5 Men's & Women's Stick & Razors Bundle     
688     Fukobuku

In [293]:
layer3[layer3['cluster']==4]['item_name']

1363    Pursonic S20 UV Family Toothbrush Sanitizer w/ AC Adapter                   
25      4-for-Tuesday: Hudson & Mane Hair Fiber Bundles                             
1483    Holmes Air Purifier                                                         
29      iRobot Roomba 650 Robotic Vacuum (Refurbished)                              
792     2-for-Tuesday: BioBidet BBC-70 Bidets                                       
344     Pursonic S750 Sonic Toothbrush with UV Sanitizer                            
511     4-for-Tuesday: Two Cool Gear Salad Kits and Two 28oz Infuser Bottles        
843     Pursonic Deluxe Plus Sonic Toothbrush with UV                               
484     Ecovacs Deebot M81 Robotic Vacuum Cleaner                                   
665     3-Pack: Xela Premium Soy Blend 7.5oz 30-Hour Candles                        
316     Little Giant 17' Titan Ladder w/ AirDeck & Wheels (Refurbished)             
759     3-Pack: Monster Cleantouch Spray for Portable Devices    

# layer3 clustering with descriptions and stories

In [448]:
layer3_all_text = layer3.apply( lambda x: x.descriptions + x.nlp_story, axis=1)
layer3_tfidf_all = nlp.tfidf_content(layer3_all_text)
layer3_pca_all = layer3_pca_2.fit_transform(layer3_tfidf_all)
layer3_kmeans = KMeans(n_clusters=5)
layer3_kmeans.fit(layer3_pca_all)
layer3['cluster'] = layer3_kmeans.labels_

/Users/boyueshen/anaconda3/lib/python3.5/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [449]:
silhouette_avg = silhouette_score(layer3_pca_all, layer3['cluster'])
silhouette_avg

0.5187853726167335

In [450]:
layer3[layer3['cluster']==0]['item_name']

0       4-or-12-pack: Inkworks Projector Pens                                         
1       Pacific Pearls 3-Piece Pendant, Ring, and Earrings Gift Set                   
4       2-for-Tuesday: Bogui Wallets with or without RFID Cards                       
5       Polk Nue Era Headphones                                                       
7       Grilling Traditions 3-Piece Pizza Stone Set                                   
8       18K Gold-Plated Heart Pendant with Diamond (1 Sapphire OR 1 Sapphire & 1 Ruby)
13      6-Pack: 50"x60" Fleece Blankets With Or Without Meh Logo                      
14      3-Pack: Model Technics Metal Puzzles                                          
15      CBD Gummy Bears (Regular or Sour)                                             
16      Lovesac Sactionals for Kids & Pets                                            
18      3-for-Tuesday: Wahl Ceramic & Gel Hot and Cold Pack                           
20      Free Hugs Shirt by ApeLad          

In [451]:
# kitchen
layer3[layer3['cluster']==1]['item_name']

6       ☕ The Process Shirt And/Or ☕ The Dream Shirt                                
9       Primula Cold Brew Coffee Maker with 2 Travel Brewers                        
94      Primula Cold Brew Coffee Maker Bundle                                       
136     Nespresso Vertuo Espresso & Coffee Machine (Refurbished)                    
179     2-for-Tuesday: Your Choice Igloo 24oz Water Bottle or 16oz Steel Tumbler    
352     2-for-Tuesday: Igloo Isabel 16oz Coffee Tumblers                            
603     Behmor Connected Temperature Control Coffee Maker                           
652     Primula Cold Brew Coffee Maker Bundle                                       
821     Blue Sky Gear 5-Piece Camping Bundle                                        
865     Hamilton Beach FlexBrew 2-Way Coffee Maker (Refurbished)                    
914     Mr. Coffee Coffee Maker with 8-Cup Thermal Carafe                           
949     Mr. Coffee 10-Cup Thermal Carafe Coffee Maker (Refurbishe

In [452]:
# socks
layer3[layer3['cluster']==2]['item_name']

44      5-Pack: EuroSock Premium Athletic Socks                        
52      Unsimply Stitched 3-Pack Socks                                 
87      12-Pack: Zeke Men's Socks                                      
115     6-Pack: Men's Funky Socks                                      
184     3-Pack: Unsimply Stitched Socks                                
211     It's Glen! Custom Socks                                        
335     Unsimply Stitched 3-Pack Socks                                 
535     Minx NY SOCK MANIA                                             
624     3-Pack Unsimply Stitched Socks                                 
749     Random Socks (5-Pack Men's or Women's, 12-Pack Boy's or Girl's)
784     12-Pack: Women's Socks                                         
796     3-Pack: FootCardigan Socks                                     
839     3-Pack: Unsimply Stitched Men's Dress Socks                    
873     6-Pack: Strollegant Socks                               

In [453]:
# also kitchen
layer3[layer3['cluster']==3]['item_name']

2       Pick 4: Angry Mills Protein-Infused Caffeinated Nut Spreads                   
3       NOTILUS Antimicrobial 3-in-1 Rain Shower Spa Combo                            
11      2-for-Tuesday: Power Precision Sous Vide with Bonus Cooking Rack              
19      KitchenAid 3.5 Cup Food Chopper & Processor                                   
36      Cuisinart Waring Pro Blade Variable Speed 2-HP Blender                        
40      SharkFLEX DuoClean Corded Ultra-Light Vacuum                                  
46      2-for-Tuesday: Posture PT Portable Posture Trainers                           
53      2-for-Tuesday: Compact 121-Piece First Aid Medical Kit                        
75      Ninja 3-in-1 Intelli-Sense Kitchen System with Auto-iQ                        
77      Coquelicots Ceramic Bath Ensemble                                             
78      3-Pack: Wahl Ceramic & Gel Hot and Cold Packs                                 
80      Ray-Ban Eyeglasses                 

In [447]:
# pillows
layer3[layer3['cluster']==4]['item_name']

83      M Cushion 18" Heated Shiatsu Massage Pillow with Bonus Decor Pillow      
116     2-for-Tuesday: Bamboo Memory Foam Travel Pillows                         
156     M Cushion 18" Heated Shiatsu Massage Pillow with Bonus Decor Pillow      
177     2-Pack: Memory Foam Knee Pillow                                          
286     Meh Face Pillows                                                         
307     M Cushion Shiatsu Massage Pillow with Optional Bonus Pillow              
310     2-for-Tuesday: Shredded Memory Foam-Filled Pillows with Bamboo Covers    
358     18" M Cushion Shiatsu Massage Pillow (with or without additional cushion)
381     Meh Face Pillows                                                         
437     Amy Miller 2-Pack 17" Sequin Pillows                                     
464     iEnjoy Down & Feather Pillows                                            
775     Contour Rest 3-in-1 Insta Cool Standard Gel Pillow                       
806     2-for-Tu

In [455]:
data['third_layer_label'] = layer3['cluster']

In [457]:
len(data)

1707

In [458]:
data.to_pickle('./clustered_data.pkl')